# Chi sono gli atleti che presentano elementi più difficili?

# 1. Importo df1set

In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
%matplotlib inline
import plotly.express as px

In [2]:
df1 = pd.read_csv("final.csv")
print(df1.shape) #214531, 19 rows, cols
df1.head(1)

(214491, 19)


competition               program  \
0  ISU European Figure Skating Championships 2017  LADIES SHORT PROGRAM   

  performance_id       athlete_name athlete_nation  rank  total_segment_score  \
0     b639d77459  Evgenia MEDVEDEVA            RUS     1                78.92   

   total_element_score  total_component_score  total_deductions   aspect_id  \
0                 42.0                  36.92               0.0  00034b9414   

   aspect_desc  element_order  element_base_value     section  \
0  Transitions            NaN                 NaN  components   

   aspect_final_score   judge_name judge_nation  judge_score  
0                9.07  Agita ABELE          LAT          9.0

In [3]:
df = df1[df1['section'] != 'components'] # Togliere gli elementi con section=components

## 2. Distribuzione dei base_value

In [4]:
# Mostra la distribuzione degli element_base_value per tutto il df1set:
#df5 = df5.sort_values(by='element_base_value', ascending=False)
# hist_df = px.histogram(
#     df, x="element_base_value",
#      title='Distribution of base values of the elements for all df1set',
#      labels={'element_base_value': 'Base value', 'count': 'Number of elements'},
#      )
# hist_df.show()

In [5]:
# Mostra la distribuzione degli element_base_value per tutti gli atleti:
# hist_df = px.histogram(
#     df, x="element_base_value", color="athlete_name",
#      title='Distribution of base values of the elements for all athletes',
#      labels={'element_base_value': 'Base value', 'athlete_name':'Athlete name'},
#      )
# hist_df.show()

Pick just a fraction of base values to make the plot more readable.

In [6]:
df["element_base_value"].describe()

count    136861.000000
mean          4.945993
std           2.621673
min           0.400000
25%           3.200000
50%           4.400000
75%           6.200000
max          17.900000
Name: element_base_value, dtype: float64

In [7]:
# Mostra la distribuzione degli element_base_value per top athletes:
hist_df = px.histogram(
    df[df["element_base_value"]>12], x="element_base_value", color='athlete_name',
     title='Distribution of base values of the elements for top athletes',
     labels={'element_base_value': 'Base value', 'athlete_name':'Athlete name'},
     )
hist_df.show()

## 3.Bubble chart base value e atleti

In [8]:
bubble_df = px.scatter(
    df[df["element_base_value"]>12], y="athlete_name", x="aspect_desc",
    color="performance_id", size="element_base_value", 
    title='Top athletes: base values of the elements for each aspect',
    hover_name="aspect_desc", log_x=False, size_max=30
    )
bubble_df.show()

In [9]:
# Add a column with the percentage of the base value of the element among top athletes:
df['element_base_value_perc'] = df['element_base_value']/df['element_base_value'].max()
df.head()
bubble2_df = px.scatter(
    df[df["element_base_value"]>12], y="athlete_name", x="aspect_desc",
    color="performance_id", size="element_base_value_perc", 
    title='Top athletes: base values of the elements for each aspect',
    hover_name="aspect_desc", log_x=False, size_max=40
    )
bubble2_df.show()

<ipython-input-9-154f718e09fe>:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



# 2. Domande aperte

* Non è detto che chi fa gli elementi più difficili sia anche il migliore e li faccia bene (vedi rank e total_deductions)
* Pick a reasonable number of base values to make the plot more readable (95 percentile ?)
* Rifare grafico Bubble con nuova colonna "percentage_of_base_value" per discrimnare meglio le size delle bolle -> non ha funzionato

- In media l'atleta x ha portato eleemnti con base value di y
- asse x atleti, size è la media del base_value, rank medio dell'ateleta (forse?)
- 90% percentile sulla media dei base_value

In [10]:
# Drop cols not interesting:
# Quante performance ci sono per ogni elemento penalizzato?
# Prima elimino le righe di doppioni di aspect_id con i diversi voti dei giudici:
df1 = df.drop_duplicates(subset=['aspect_id', 'performance_id'])
# Elimina le colonne che non servono:
df1 = df1.drop(['judge_name', 'judge_nation', 'judge_score', 'section'], axis=1)

# Raggruppo per athlete_name e calcolo la media degli element_base_value di ciascun athlete_name sotto la colonna 'avg_element_base_value':
df2 = df1.groupby(['athlete_name']).mean().reset_index()
df2.drop(['total_segment_score','total_element_score','total_component_score','total_deductions','element_order','aspect_final_score','element_base_value_perc'], axis=1)
df2 = df2.sort_values(by='element_base_value', ascending=False)
# Rename col element_base_value to avg_element_base_value:
df2.rename(columns={'element_base_value': 'avg_elem_base_value', 'rank': 'avg_rank'}, inplace=True)

# Aggiungo la colonna avg_elem_base_value di df2 al df1frame df1 matchando per athlete_name:
df1 = pd.merge(df1, df2, on='athlete_name')

In [11]:
df1.head()

competition               program  \
0  ISU European Figure Skating Championships 2017  LADIES SHORT PROGRAM   
1  ISU European Figure Skating Championships 2017  LADIES SHORT PROGRAM   
2  ISU European Figure Skating Championships 2017  LADIES SHORT PROGRAM   
3  ISU European Figure Skating Championships 2017  LADIES SHORT PROGRAM   
4  ISU European Figure Skating Championships 2017  LADIES SHORT PROGRAM   

  performance_id       athlete_name athlete_nation  rank  \
0     b639d77459  Evgenia MEDVEDEVA            RUS     1   
1     b639d77459  Evgenia MEDVEDEVA            RUS     1   
2     b639d77459  Evgenia MEDVEDEVA            RUS     1   
3     b639d77459  Evgenia MEDVEDEVA            RUS     1   
4     b639d77459  Evgenia MEDVEDEVA            RUS     1   

   total_segment_score_x  total_element_score_x  total_component_score_x  \
0                  78.92                   42.0                    36.92   
1                  78.92                   42.0                    36.92   
2                  78.92                   42.0                    36.92   
3                  78.92                   42.0                    36.92   
4                  78.92                   42.0                    36.92   

   total_deductions_x  ... element_base_value_perc_x avg_rank  \
0                 0.0  ...                  0.313408      1.0   
1                 0.0  ...                  0.589944      1.0   
2                 0.0  ...                  0.195531      1.0   
3                 0.0  ...                  0.202793      1.0   
4                 0.0  ...                  0.178771      1.0   

   total_segment_score_y  total_element_score_y  total_component_score_y  \
0             122.553684              62.344135                60.480226   
1             122.553684              62.344135                60.480226   
2             122.553684              62.344135                60.480226   
3             122.553684              62.344135                60.480226   
4             122.553684              62.344135                60.480226   

   total_deductions_y  element_order_y  avg_elem_base_value  \
0            0.270677         5.578947             5.012632   
1            0.270677         5.578947             5.012632   
2            0.270677         5.578947             5.012632   
3            0.270677         5.578947             5.012632   
4            0.270677         5.578947             5.012632   

   aspect_final_score_y  element_base_value_perc_y  
0              6.117744                   0.280035  
1              6.117744                   0.280035  
2              6.117744                   0.280035  
3              6.117744                   0.280035  
4              6.117744                   0.280035  

[5 rows x 25 columns]

In [12]:
bubble_df1 = px.scatter(
    df1, y="athlete_name", x="avg_elem_base_value",
    color="program", #size="avg_elem_base_value", 
    title='Base values of the elements for each aspect',
    hover_name="aspect_desc", log_x=False, size_max=60
    )
bubble_df1.update_layout(height=1000)
bubble_df1.show()


In [13]:
bubble2_df1 = px.scatter(
    df1, y="athlete_name", x="avg_elem_base_value",
    color="program", size="avg_rank", 
    title='Base values of the elements for each aspect',
    hover_name="aspect_desc", log_x=False, size_max=60
    )
bubble2_df1.update_layout(height=1000)
bubble2_df1.show()

# 3. Domande aperte

* Unisci categorie 
* scambia size

In [14]:
# new categories
conditions = [
    (df1['program'] == "LADIES SHORT PROGRAM") |
    (df1['program'] == "JUNIOR LADIES SHORT PROGRAM") |
    (df1['program'] == "JUNIOR LADIES FREE SKATING") |
    (df1['program'] == "LADIES FREE SKATING"),

    (df1['program'] == "MEN SHORT PROGRAM") |
    (df1['program'] == "JUNIOR MEN SHORT PROGRAM") |
    (df1['program'] == "MEN FREE SKATING") |
    (df1['program'] == "JUNIOR MEN FREE SKATING"),

    (df1['program'] == "PAIRS SHORT PROGRAM") |
    (df1['program'] == "JUNIOR PAIRS SHORT PROGRAM") |
    (df1['program'] == "PAIRS FREE SKATING") |
    (df1['program'] == "JUNIOR PAIRS FREE SKATING"),

    (df1['program'] == "ICE DANCE SHORT DANCE") |
    (df1['program'] == "JUNIOR ICE DANCE SHORT DANCE") |
    (df1['program'] == "ICE DANCE FREE DANCE") |
    (df1['program'] == "JUNIOR ICE DANCE FREE DANCE"),

    ]

# create a list of the values we want to assign for each condition
values = ['Ladies','Men','Pairs','Ice dance']

# create a new column and use np.select to assign values to it using our lists as arguments
df1['category'] = np.select(conditions, values)

# display updated DataFrame
df1.head(1)

competition               program  \
0  ISU European Figure Skating Championships 2017  LADIES SHORT PROGRAM   
1  ISU European Figure Skating Championships 2017  LADIES SHORT PROGRAM   
2  ISU European Figure Skating Championships 2017  LADIES SHORT PROGRAM   
3  ISU European Figure Skating Championships 2017  LADIES SHORT PROGRAM   
4  ISU European Figure Skating Championships 2017  LADIES SHORT PROGRAM   

  performance_id       athlete_name athlete_nation  rank  \
0     b639d77459  Evgenia MEDVEDEVA            RUS     1   
1     b639d77459  Evgenia MEDVEDEVA            RUS     1   
2     b639d77459  Evgenia MEDVEDEVA            RUS     1   
3     b639d77459  Evgenia MEDVEDEVA            RUS     1   
4     b639d77459  Evgenia MEDVEDEVA            RUS     1   

   total_segment_score_x  total_element_score_x  total_component_score_x  \
0                  78.92                   42.0                    36.92   
1                  78.92                   42.0                    36.92   
2                  78.92                   42.0                    36.92   
3                  78.92                   42.0                    36.92   
4                  78.92                   42.0                    36.92   

   total_deductions_x  ... avg_rank total_segment_score_y  \
0                 0.0  ...      1.0            122.553684   
1                 0.0  ...      1.0            122.553684   
2                 0.0  ...      1.0            122.553684   
3                 0.0  ...      1.0            122.553684   
4                 0.0  ...      1.0            122.553684   

   total_element_score_y  total_component_score_y  total_deductions_y  \
0              62.344135                60.480226            0.270677   
1              62.344135                60.480226            0.270677   
2              62.344135                60.480226            0.270677   
3              62.344135                60.480226            0.270677   
4              62.344135                60.480226            0.270677   

   element_order_y  avg_elem_base_value  aspect_final_score_y  \
0         5.578947             5.012632              6.117744   
1         5.578947             5.012632              6.117744   
2         5.578947             5.012632              6.117744   
3         5.578947             5.012632              6.117744   
4         5.578947             5.012632              6.117744   

   element_base_value_perc_y  category  
0                   0.280035    Ladies  
1                   0.280035    Ladies  
2                   0.280035    Ladies  
3                   0.280035    Ladies  
4                   0.280035    Ladies  

[5 rows x 26 columns]

In [15]:
# Ordino data secondo il rank in modo rescente:
df1 = df1.sort_values(by=['avg_rank'], ascending=True)
# Create a new column with the inverse of the rank:
df1['avg_rank_inv'] = 1/df1['avg_rank']
df1.head(1)

competition               program  \
0  ISU European Figure Skating Championships 2017  LADIES SHORT PROGRAM   

  performance_id       athlete_name athlete_nation  rank  \
0     b639d77459  Evgenia MEDVEDEVA            RUS     1   

   total_segment_score_x  total_element_score_x  total_component_score_x  \
0                  78.92                   42.0                    36.92   

   total_deductions_x  ... total_segment_score_y total_element_score_y  \
0                 0.0  ...            122.553684             62.344135   

   total_component_score_y  total_deductions_y  element_order_y  \
0                60.480226            0.270677         5.578947   

   avg_elem_base_value  aspect_final_score_y  element_base_value_perc_y  \
0             5.012632              6.117744                   0.280035   

   category  avg_rank_inv  
0    Ladies           1.0  

[1 rows x 27 columns]

In [18]:
bubble3_df1 = px.scatter(
    df1, y="athlete_name", x="avg_elem_base_value",
    color="category", size="avg_rank_inv", 
    title='Base values of the elements for each aspect',
    hover_name="aspect_desc", log_x=False, size_max=60,
    labels={
        "category": "Category",  
        "avg_rank": "Average rank", 
        "program": "Program",
    },
    hover_data={"program":True, "avg_rank_inv":False, "avg_rank": True},
    category_orders={ # replaces default order by column name
        "category": ['Ladies','Men','Pairs','Ice dance']
    },
    )
bubble3_df1.update_traces(
    marker=dict(symbol="star", line=dict(width=0.5, color='DarkSlateGrey')),
    selector=dict(mode="markers")
    )
bubble3_df1.update_layout(height=1000)
bubble3_df1.show()